In [24]:
import pandas as pd

In [25]:
binance_df = pd.read_csv('cex.csv')
nostra_df = pd.read_csv('nostra-eth-usdc.csv')
blocks_df = pd.read_csv('blocks.csv')

/var/folders/zp/9kkn3ltx55q4wz7hp7q19ggm0000gn/T/ipykernel_5689/2196764896.py:3: DtypeWarning: Columns (14) have mixed types. Specify dtype option on import or set low_memory=False.
  blocks_df = pd.read_csv('blocks.csv')


In [26]:
binance_df.head()

Date        Id    Price     Qty     Base_Qty  \
0  2023-12-01 01:00:08.773000  32430895  2052.80  2.5145  5161.765600   
1  2023-12-01 01:00:08.779000  32430896  2052.80  1.7054  3500.845120   
2  2023-12-01 01:00:11.071000  32430897  2053.12  0.3839   788.192768   
3  2023-12-01 01:00:11.085000  32430898  2053.12  0.3859   792.299008   
4  2023-12-01 01:00:11.984000  32430899  2053.12  0.1700   349.030400   

            Time  is_buyer_maker  Unknown  
0  1701388808773           False     True  
1  1701388808779           False     True  
2  1701388811071            True     True  
3  1701388811085            True     True  
4  1701388811984            True     True

In [27]:
nostra_df.head()

block_number  transaction_index  event_index  \
0        602284                 70            6   
1        628042                120            6   
2        660001                 47            7   
3        660001                 47            8   
4        660001                125            7   

                                          class_hash  \
0  04f9849485e35f4a1c57d69b297feda94e743151f78820...   
1  04f9849485e35f4a1c57d69b297feda94e743151f78820...   
2  04f9849485e35f4a1c57d69b297feda94e743151f78820...   
3  04f9849485e35f4a1c57d69b297feda94e743151f78820...   
4  04f9849485e35f4a1c57d69b297feda94e743151f78820...   

                                    contract_address  \
0  05ef8800d242c5d5e218605d6a10e81449529d4144185f...   
1  05ef8800d242c5d5e218605d6a10e81449529d4144185f...   
2  05ef8800d242c5d5e218605d6a10e81449529d4144185f...   
3  05ef8800d242c5d5e218605d6a10e81449529d4144185f...   
4  05ef8800d242c5d5e218605d6a10e81449529d4144185f...   

                                                keys  \
0  {"\\x00e14a408baf7f453312eec68e9b7d728ec5337fb...   
1  {"\\x00e14a408baf7f453312eec68e9b7d728ec5337fb...   
2  {"\\x00e14a408baf7f453312eec68e9b7d728ec5337fb...   
3  {"\\x00e316f0d9d2a3affa97de1d99bb2aac0538e2666...   
4  {"\\x00e14a408baf7f453312eec68e9b7d728ec5337fb...   

                                                data event_name  \
0  {"\\x08d27bea7c176d9903","\\x00","\\x9073251f0...       Sync   
1  {"\\x03b253b20be774a452","\\x00","\\x38d5cc00a...       Sync   
2  {"\\xee6a4687eb3e20d9","\\x00","\\x0e02b83f6a"...       Sync   
3  {"\\x049ff5b3a7d38e2b50198f408fa8281635b5bc81e...       Swap   
4  {"\\xee698b3e1a75ec81","\\x00","\\x0e02c343d6"...       Sync   

                                        decoded_data  
0  {"reserve_0": 162740926578466593027, "reserve_...  
1  {"reserve_0": 68190042147144377426, "reserve_1...  
2  {"reserve_0": 17179621278139424985, "reserve_1...  
3  {"to": "0x04270219d365d6b017231b52e92b3fb5d7c8...  
4  {"reserve_0": 17179415352429636737, "reserve_1...

In [28]:
nostra_df = nostra_df[nostra_df['block_number'] <= 636977]

In [30]:
blocks_df.set_index('block_number', inplace=True)
nostra_df['timestamp'] = nostra_df['block_number'].map(blocks_df['timestamp'])

In [31]:
nostra_df.timestamp.isna().sum()

np.int64(0)

In [35]:
swap_mask = nostra_df['event_name'] == "Swap"
sync_mask = nostra_df['event_name'] == "Sync"

In [36]:
import json

def get_price_from_data(decoded_data):
    data = json.loads(decoded_data)

    eth = data['reserve_0'] / 10**18 if data['reserve_0'] > 0 else data['reserve_0']
    usdc = data['reserve_1'] / 10**6 if data['reserve_1'] > 0 else data['reserve_1']

    print("usdc: ", usdc)
    print("eth: ", eth)
    print("price: ", usdc / eth)

    return usdc / eth

In [40]:
# Test
print(nostra_df['block_number'])
get_price_from_data(nostra_df.loc[sync_mask,'decoded_data'][0])

0         602284
1         628042
27        514755
28        514800
29        514800
           ...  
367656    579988
367657    579992
367658    579992
367660    579996
367661    579996
Name: block_number, Length: 259834, dtype: int64
usdc:  620407.103246
eth:  162.7409265784666
price:  3812.2377467653578


3812.2377467653578

1. Order by block_number, tx_index, event_index
2. Merge liquidity from Syncs with Swaps
3. 

In [42]:
sync_data = nostra_df[sync_mask]
sync_data['price'] = sync_data['decoded_data'].apply(get_price_from_data)

usdc:  620407.103246
eth:  162.7409265784666
price:  3812.2377467653578
usdc:  244105.085089
eth:  68.19004214714438
price:  3579.776128635557
usdc:  2.5
eth:  0.001048
price:  2385.4961832061067
usdc:  4.885496
eth:  0.002048
price:  2385.49609375
usdc:  4.289123
eth:  0.001798000009831399
price:  2385.4966499150337
usdc:  3.650407
eth:  0.001530250020367072
price:  2385.4971092399337
usdc:  3.203127
eth:  0.00134275002774574
price:  2385.4976233942307
usdc:  2.915526
eth:  0.001222187532495609
price:  2385.498070043907
usdc:  2.811646
eth:  0.001178640659213344
price:  2385.4989033524157
usdc:  2.733736
eth:  0.001145980504241408
price:  2385.4995699160004
usdc:  5.119234
eth:  0.002145979846133554
price:  2385.4995699160013
usdc:  38761.886283
eth:  17.58228522724008
price:  2204.5988779061863
usdc:  39261.886282
eth:  17.80908385487745
price:  2204.598877850035
usdc:  99982.815818
eth:  44.169711150866775
price:  2263.605833338984
usdc:  39291.874171
eth:  17.822686279473274
price:

/var/folders/zp/9kkn3ltx55q4wz7hp7q19ggm0000gn/T/ipykernel_5689/128387230.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  sync_data['price'] = sync_data['decoded_data'].apply(get_price_from_data)


In [44]:
sync_data['usdc_liquidity'] = sync_data['decoded_data'].apply(lambda x: json.loads(x)['reserve_1'] / 10**6)
sync_data['eth_liquidity'] = sync_data['decoded_data'].apply(lambda x: json.loads(x)['reserve_0'] / 10**18)

/var/folders/zp/9kkn3ltx55q4wz7hp7q19ggm0000gn/T/ipykernel_5689/1966536774.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  sync_data['usdc_liquidity'] = sync_data['decoded_data'].apply(lambda x: json.loads(x)['reserve_1'] / 10**6)
/var/folders/zp/9kkn3ltx55q4wz7hp7q19ggm0000gn/T/ipykernel_5689/1966536774.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  sync_data['eth_liquidity'] = sync_data['decoded_data'].apply(lambda x: json.loads(x)['reserve_0'] / 10**18)


In [45]:
sync_data.head()

block_number  transaction_index  event_index  \
0         602284                 70            6   
1         628042                120            6   
30        514800                 35            4   
33        514836                 48            5   
39        514837                 22            6   

                                           class_hash  \
0   04f9849485e35f4a1c57d69b297feda94e743151f78820...   
1   04f9849485e35f4a1c57d69b297feda94e743151f78820...   
30  0652ad70e5978e84fb886ebe5a0a85f2352281b67488b4...   
33  0652ad70e5978e84fb886ebe5a0a85f2352281b67488b4...   
39  0652ad70e5978e84fb886ebe5a0a85f2352281b67488b4...   

                                     contract_address  \
0   05ef8800d242c5d5e218605d6a10e81449529d4144185f...   
1   05ef8800d242c5d5e218605d6a10e81449529d4144185f...   
30  05ef8800d242c5d5e218605d6a10e81449529d4144185f...   
33  05ef8800d242c5d5e218605d6a10e81449529d4144185f...   
39  05ef8800d242c5d5e218605d6a10e81449529d4144185f...   

                                                 keys  \
0   {"\\x00e14a408baf7f453312eec68e9b7d728ec5337fb...   
1   {"\\x00e14a408baf7f453312eec68e9b7d728ec5337fb...   
30  {"\\x00e14a408baf7f453312eec68e9b7d728ec5337fb...   
33  {"\\x00e14a408baf7f453312eec68e9b7d728ec5337fb...   
39  {"\\x00e14a408baf7f453312eec68e9b7d728ec5337fb...   

                                                 data event_name  \
0   {"\\x08d27bea7c176d9903","\\x00","\\x9073251f0...       Sync   
1   {"\\x03b253b20be774a452","\\x00","\\x38d5cc00a...       Sync   
30  {"\\x03b92683b98000","\\x00","\\x2625a0","\\x00"}       Sync   
33  {"\\x0746a528800000","\\x00","\\x4a8bf8","\\x00"}       Sync   
39  {"\\x0663457fe463e7","\\x00","\\x417263","\\x00"}       Sync   

                                         decoded_data   timestamp  \
0   {"reserve_0": 162740926578466593027, "reserve_...  1709771770   
1   {"reserve_0": 68190042147144377426, "reserve_1...  1711609199   
30  {"reserve_0": 1048000000000000, "reserve_1": 2...  1705932348   
33  {"reserve_0": 2048000000000000, "reserve_1": 4...  1705934246   
39  {"reserve_0": 1798000009831399, "reserve_1": 4...  1705934303   

          price  usdc_liquidity  eth_liquidity  
0   3812.237747   620407.103246     162.740927  
1   3579.776129   244105.085089      68.190042  
30  2385.496183        2.500000       0.001048  
33  2385.496094        4.885496       0.002048  
39  2385.496650        4.289123       0.001798

In [47]:
sync_data[sync_data.eth_liquidity == sync_data['eth_liquidity'].min()]

block_number  transaction_index  event_index  \
30        514800                 35            4   

                                           class_hash  \
30  0652ad70e5978e84fb886ebe5a0a85f2352281b67488b4...   

                                     contract_address  \
30  05ef8800d242c5d5e218605d6a10e81449529d4144185f...   

                                                 keys  \
30  {"\\x00e14a408baf7f453312eec68e9b7d728ec5337fb...   

                                                 data event_name  \
30  {"\\x03b92683b98000","\\x00","\\x2625a0","\\x00"}       Sync   

                                         decoded_data   timestamp  \
30  {"reserve_0": 1048000000000000, "reserve_1": 2...  1705932348   

          price  usdc_liquidity  eth_liquidity  
30  2385.496183             2.5       0.001048

In [48]:
sync_data.block_number.min()

np.int64(514800)

In [52]:
sync_data = sync_data.sort_values('block_number', ascending=False)

In [53]:
sync_data.head()

block_number  transaction_index  event_index  \
258585        636975                 33            7   
258589        636975                 89            7   
258581        636974                186            7   
258573        636973                105            7   
258536        636971                 47           10   

                                               class_hash  \
258585  04f9849485e35f4a1c57d69b297feda94e743151f78820...   
258589  04f9849485e35f4a1c57d69b297feda94e743151f78820...   
258581  04f9849485e35f4a1c57d69b297feda94e743151f78820...   
258573  04f9849485e35f4a1c57d69b297feda94e743151f78820...   
258536  04f9849485e35f4a1c57d69b297feda94e743151f78820...   

                                         contract_address  \
258585  05ef8800d242c5d5e218605d6a10e81449529d4144185f...   
258589  05ef8800d242c5d5e218605d6a10e81449529d4144185f...   
258581  05ef8800d242c5d5e218605d6a10e81449529d4144185f...   
258573  05ef8800d242c5d5e218605d6a10e81449529d4144185f...   
258536  05ef8800d242c5d5e218605d6a10e81449529d4144185f...   

                                                     keys  \
258585  {"\\x00e14a408baf7f453312eec68e9b7d728ec5337fb...   
258589  {"\\x00e14a408baf7f453312eec68e9b7d728ec5337fb...   
258581  {"\\x00e14a408baf7f453312eec68e9b7d728ec5337fb...   
258573  {"\\x00e14a408baf7f453312eec68e9b7d728ec5337fb...   
258536  {"\\x00e14a408baf7f453312eec68e9b7d728ec5337fb...   

                                                     data event_name  \
258585  {"\\x02c783466a8064ef8b","\\x00","\\x23908dd4a...       Sync   
258589  {"\\x02c73c3b266c2f4f2d","\\x00","\\x23941c2db...       Sync   
258581  {"\\x02c7839f6dd1ad1cf9","\\x00","\\x239089608...       Sync   
258573  {"\\x02c783a2e0063b217c","\\x00","\\x239089346...       Sync   
258536  {"\\x02c7fa8dcfdc9a6cf8","\\x00","\\x238a97014...       Sync   

                                             decoded_data   timestamp  \
258585  {"reserve_0": 51269900006150434699, "reserve_1...  1714513290   
258589  {"reserve_0": 51249902895779237677, "reserve_1...  1714513290   
258581  {"reserve_0": 51269997876933893369, "reserve_1...  1714512924   
258573  {"reserve_0": 51270001665976770940, "reserve_1...  1714512558   
258536  {"reserve_0": 51303474029043281144, "reserve_1...  1714511816   

              price  usdc_liquidity  eth_liquidity  
258585  2979.312803   152749.069486      51.269900  
258589  2981.639406   152808.730040      51.249903  
258581  2979.301423   152748.777607      51.269998  
258573  2979.300982   152748.766307      51.270002  
258536  2975.412685   152649.007433      51.303474

In [54]:
result_df = sync_data
result_df_sorted = result_df.sort_values(by=['block_number', 'transaction_index', 'event_index'], ascending=[True, False, False])
result_df_unique = result_df_sorted.drop_duplicates(subset=['block_number'], keep='first')

result_df_unique.head()

block_number  transaction_index  event_index  \
30        514800                 35            4   
33        514836                 48            5   
39        514837                 22            6   
44        514965                 92            6   
57        514966                 29            6   

                                           class_hash  \
30  0652ad70e5978e84fb886ebe5a0a85f2352281b67488b4...   
33  0652ad70e5978e84fb886ebe5a0a85f2352281b67488b4...   
39  0652ad70e5978e84fb886ebe5a0a85f2352281b67488b4...   
44  0652ad70e5978e84fb886ebe5a0a85f2352281b67488b4...   
57  0652ad70e5978e84fb886ebe5a0a85f2352281b67488b4...   

                                     contract_address  \
30  05ef8800d242c5d5e218605d6a10e81449529d4144185f...   
33  05ef8800d242c5d5e218605d6a10e81449529d4144185f...   
39  05ef8800d242c5d5e218605d6a10e81449529d4144185f...   
44  05ef8800d242c5d5e218605d6a10e81449529d4144185f...   
57  05ef8800d242c5d5e218605d6a10e81449529d4144185f...   

                                                 keys  \
30  {"\\x00e14a408baf7f453312eec68e9b7d728ec5337fb...   
33  {"\\x00e14a408baf7f453312eec68e9b7d728ec5337fb...   
39  {"\\x00e14a408baf7f453312eec68e9b7d728ec5337fb...   
44  {"\\x00e14a408baf7f453312eec68e9b7d728ec5337fb...   
57  {"\\x00e14a408baf7f453312eec68e9b7d728ec5337fb...   

                                                 data event_name  \
30  {"\\x03b92683b98000","\\x00","\\x2625a0","\\x00"}       Sync   
33  {"\\x0746a528800000","\\x00","\\x4a8bf8","\\x00"}       Sync   
39  {"\\x0663457fe463e7","\\x00","\\x417263","\\x00"}       Sync   
44  {"\\x056fc118e1aae0","\\x00","\\x37b367","\\x00"}       Sync   
57  {"\\x045792b5b92af9","\\x00","\\x2c7cc6","\\x00"}       Sync   

                                         decoded_data   timestamp  \
30  {"reserve_0": 1048000000000000, "reserve_1": 2...  1705932348   
33  {"reserve_0": 2048000000000000, "reserve_1": 4...  1705934246   
39  {"reserve_0": 1798000009831399, "reserve_1": 4...  1705934303   
44  {"reserve_0": 1530250020367072, "reserve_1": 3...  1705943623   
57  {"reserve_0": 1222187532495609, "reserve_1": 2...  1705943730   

          price  usdc_liquidity  eth_liquidity  
30  2385.496183        2.500000       0.001048  
33  2385.496094        4.885496       0.002048  
39  2385.496650        4.289123       0.001798  
44  2385.497109        3.650407       0.001530  
57  2385.498070        2.915526       0.001222

In [56]:
result = result_df_unique[['block_number', 'timestamp', 'price', 'usdc_liquidity', 'eth_liquidity']]

In [57]:
result.head()

block_number   timestamp        price  usdc_liquidity  eth_liquidity
30        514800  1705932348  2385.496183        2.500000       0.001048
33        514836  1705934246  2385.496094        4.885496       0.002048
39        514837  1705934303  2385.496650        4.289123       0.001798
44        514965  1705943623  2385.497109        3.650407       0.001530
57        514966  1705943730  2385.498070        2.915526       0.001222

In [58]:
complete_result = pd.merge(blocks_df, result, on='block_number', how='left')
complete_result.head()

block_number  Unnamed: 0  timestamp_x  \
0        480000           0   1703446511   
1        480001           1   1703446609   
2        480002           2   1703446680   
3        480003           3   1703446744   
4        480004           4   1703446828   

                                          block_hash  \
0  0x03ef0086ed307d8e10cbac8b81e6d60b32f81b10e38d...   
1  0x02cbc277b913626e47a2b4ddefe9c106d576ff312e12...   
2  0x0434e1451ba020b37b4b72e53b80d1e9721ab6d81377...   
3  0x06d90b411e20e8405e546cff91773fac625d5a81f867...   
4  0x0247bf05c7c99dd8a1632d3de56ad7c88bde8f7d1c36...   

                                         parent_hash  \
0  0x0236f316b337c44044867da7cc341f21c5cd3122d7c8...   
1  0x03ef0086ed307d8e10cbac8b81e6d60b32f81b10e38d...   
2  0x02cbc277b913626e47a2b4ddefe9c106d576ff312e12...   
3  0x0434e1451ba020b37b4b72e53b80d1e9721ab6d81377...   
4  0x06d90b411e20e8405e546cff91773fac625d5a81f867...   

                                            new_root  \
0  0x0359e09a14ca686f2fcf1c183ff0daf371bf6e982dc2...   
1  0x00cb69d962d887f2b60f452cd41af445d889287f2898...   
2  0x02d3002c29eebd67aba749baf0ed3bf448f7a019d810...   
3  0x0316d25e24545beb99b9870f8f0c487854967675a0cf...   
4  0x04096444ae78c9a45b84c8d7b055122258c5c744f4d5...   

                                   sequencer_address  l1_gas_price_wei  \
0  0x01176a1bd84444c89232ec27754698e5d2e7e1a7f153...       19512574037   
1  0x01176a1bd84444c89232ec27754698e5d2e7e1a7f153...       19474429052   
2  0x01176a1bd84444c89232ec27754698e5d2e7e1a7f153...       19453296549   
3  0x01176a1bd84444c89232ec27754698e5d2e7e1a7f153...       19423239765   
4  0x01176a1bd84444c89232ec27754698e5d2e7e1a7f153...       19415676669   

   l1_gas_price_fri  l1_data_gas_price_wei  l1_data_gas_price_fri l1_da_mode  \
0                 0                      0                      0   CALLDATA   
1                 0                      0                      0   CALLDATA   
2                 0                      0                      0   CALLDATA   
3                 0                      0                      0   CALLDATA   
4                 0                      0                      0   CALLDATA   

  starknet_version  transaction_count          total_fee  timestamp_y  price  \
0           0.12.3                119  25294383875051544          NaN    NaN   
1           0.12.3                120  27153679927270967          NaN    NaN   
2           0.12.3                 98  23914462686692523          NaN    NaN   
3           0.12.3                273  35953018925447715          NaN    NaN   
4           0.12.3                153  21857139763096743          NaN    NaN   

   usdc_liquidity  eth_liquidity  
0             NaN            NaN  
1             NaN            NaN  
2             NaN            NaN  
3             NaN            NaN  
4             NaN            NaN

In [59]:
complete_result = complete_result[['block_number', 'timestamp_x', 'price', 'usdc_liquidity', 'eth_liquidity']]

In [66]:
complete_result.shape[0]

160000

In [61]:
complete_result.loc[complete_result['block_number'] == 480000, 'price'] = 0
complete_result.loc[complete_result['block_number'] == 480000, 'usdc_liquidity'] = 0
complete_result.loc[complete_result['block_number'] == 480000, 'eth_liquidity'] = 0

In [65]:
complete_result[complete_result['block_number'] > 550000].head()

block_number  timestamp_x        price  usdc_liquidity  eth_liquidity
70001        550001   1708087903  2836.425189   313046.029306     110.366397
70002        550002   1708087950  2836.425189   313046.029306     110.366397
70003        550003   1708087970  2837.383739   313098.947172     110.347763
70004        550004   1708088005  2837.383739   313098.947172     110.347763
70005        550005   1708088010  2837.383739   313098.947172     110.347763

In [67]:
complete_result.head()

block_number  timestamp_x  price  usdc_liquidity  eth_liquidity
0        480000   1703446511    0.0             0.0            0.0
1        480001   1703446609    0.0             0.0            0.0
2        480002   1703446680    0.0             0.0            0.0
3        480003   1703446744    0.0             0.0            0.0
4        480004   1703446828    0.0             0.0            0.0

In [64]:
complete_result.fillna(method='ffill', inplace=True)

/var/folders/zp/9kkn3ltx55q4wz7hp7q19ggm0000gn/T/ipykernel_5689/3019128003.py:2: FutureWarning: DataFrame.fillna with 'method' is deprecated and will raise in a future version. Use obj.ffill() or obj.bfill() instead.
  complete_result.fillna(method='ffill', inplace=True)


In [68]:
binance_df.head()

Date        Id    Price     Qty     Base_Qty  \
0  2023-12-01 01:00:08.773000  32430895  2052.80  2.5145  5161.765600   
1  2023-12-01 01:00:08.779000  32430896  2052.80  1.7054  3500.845120   
2  2023-12-01 01:00:11.071000  32430897  2053.12  0.3839   788.192768   
3  2023-12-01 01:00:11.085000  32430898  2053.12  0.3859   792.299008   
4  2023-12-01 01:00:11.984000  32430899  2053.12  0.1700   349.030400   

            Time  is_buyer_maker  Unknown  
0  1701388808773           False     True  
1  1701388808779           False     True  
2  1701388811071            True     True  
3  1701388811085            True     True  
4  1701388811984            True     True

In [73]:
result_copy = complete_result.copy()

In [75]:
binance_df.drop_duplicates(subset='Time', inplace=True)

In [84]:
result_copy['timestamp_pd'] = pd.to_datetime(result_copy['timestamp_x'], unit='s')

In [89]:
binance_df['time_pd'] = pd.to_datetime(binance_df['Time'], unit='ms')

In [96]:
result_copy['timestamp_pd'].min()

'2023-12-24 19:35:11'

In [97]:
binance_df['time_pd'].min()

'2023-12-01 00:00:08'

In [100]:
result_copy['timestamp_pd'] = pd.to_datetime(result_copy['timestamp_pd'])
binance_df['time_pd'] = pd.to_datetime(binance_df['time_pd'])

result_copy['timestamp_pd'] = result_copy['timestamp_pd'].dt.tz_localize('UTC')
binance_df['time_pd'] = binance_df['time_pd'].dt.tz_localize('UTC')

In [101]:
merged_df = pd.merge_asof(result_copy.sort_values('timestamp_pd'), binance_df.sort_values('time_pd'), left_on='timestamp_pd', right_on='time_pd', direction='forward')

In [102]:
merged_df.head()

block_number  timestamp_x  price  usdc_liquidity  eth_liquidity  \
0        480000   1703446511    0.0             0.0            0.0   
1        480001   1703446609    0.0             0.0            0.0   
2        480002   1703446680    0.0             0.0            0.0   
3        480003   1703446744    0.0             0.0            0.0   
4        480004   1703446828    0.0             0.0            0.0   

   price_binance              timestamp_pd                        Date  \
0            NaN 2023-12-24 19:35:11+00:00  2023-12-24 20:35:17.259000   
1            NaN 2023-12-24 19:36:49+00:00  2023-12-24 20:36:54.648000   
2            NaN 2023-12-24 19:38:00+00:00  2023-12-24 20:38:02.737000   
3            NaN 2023-12-24 19:39:04+00:00  2023-12-24 20:39:27.306000   
4            NaN 2023-12-24 19:40:28+00:00  2023-12-24 20:40:28.417000   

         Id    Price     Qty    Base_Qty           Time  is_buyer_maker  \
0  33003769  2292.37  0.3733  855.741721  1703446517259            True   
1  33003791  2287.87  0.0747  170.903889  1703446614648            True   
2  33003817  2285.64  0.0888  202.964832  1703446682737           False   
3  33003840  2285.39  0.0134   30.624226  1703446767306            True   
4  33003847  2284.53  0.1100  251.298300  1703446828417           False   

   Unknown                   time_pd  
0     True 2023-12-24 19:35:17+00:00  
1     True 2023-12-24 19:36:54+00:00  
2     True 2023-12-24 19:38:02+00:00  
3     True 2023-12-24 19:39:27+00:00  
4     True 2023-12-24 19:40:28+00:00

In [103]:
merged_df.shape[0]

160000

In [104]:
merged_df.rename(columns={'price': 'price_nostra', 'Price': 'price_binance', 'timestamp_pd': 'datetime_utc'}, inplace=True)

In [106]:
final = merged_df[['block_number', 'datetime_utc', 'price_nostra', 'price_binance', 'usdc_liquidity', 'eth_liquidity']]

In [95]:
result_copy['timestamp_pd'] = result_copy['timestamp_pd'].dt.strftime('%Y-%m-%d %H:%M:%S')
binance_df['time_pd'] = binance_df['time_pd'].dt.strftime('%Y-%m-%d %H:%M:%S')

AttributeError: Can only use .dt accessor with datetimelike values

In [72]:
result.head()

Empty DataFrame
Columns: [block_number, timestamp_x, price, usdc_liquidity, eth_liquidity, Date, Id, Price, Qty, Base_Qty, Time, is_buyer_maker, Unknown]
Index: []

In [107]:
final.head()

block_number              datetime_utc  price_nostra  price_binance  \
0        480000 2023-12-24 19:35:11+00:00           0.0            NaN   
1        480001 2023-12-24 19:36:49+00:00           0.0            NaN   
2        480002 2023-12-24 19:38:00+00:00           0.0            NaN   
3        480003 2023-12-24 19:39:04+00:00           0.0            NaN   
4        480004 2023-12-24 19:40:28+00:00           0.0            NaN   

   price_binance  usdc_liquidity  eth_liquidity  
0        2292.37             0.0            0.0  
1        2287.87             0.0            0.0  
2        2285.64             0.0            0.0  
3        2285.39             0.0            0.0  
4        2284.53             0.0            0.0

In [108]:
final.shape[0]

160000

In [111]:
final.to_csv('binance_nostra_eth_usdc_processed.csv', index=False)

In [112]:
nostra_df.head()

block_number  transaction_index  event_index  \
0         602284                 70            6   
1         628042                120            6   
27        514755                 26            0   
28        514800                 35            2   
29        514800                 35            3   

                                           class_hash  \
0   04f9849485e35f4a1c57d69b297feda94e743151f78820...   
1   04f9849485e35f4a1c57d69b297feda94e743151f78820...   
27  0652ad70e5978e84fb886ebe5a0a85f2352281b67488b4...   
28  0652ad70e5978e84fb886ebe5a0a85f2352281b67488b4...   
29  0652ad70e5978e84fb886ebe5a0a85f2352281b67488b4...   

                                     contract_address  \
0   05ef8800d242c5d5e218605d6a10e81449529d4144185f...   
1   05ef8800d242c5d5e218605d6a10e81449529d4144185f...   
27  05ef8800d242c5d5e218605d6a10e81449529d4144185f...   
28  05ef8800d242c5d5e218605d6a10e81449529d4144185f...   
29  05ef8800d242c5d5e218605d6a10e81449529d4144185f...   

                                                 keys  \
0   {"\\x00e14a408baf7f453312eec68e9b7d728ec5337fb...   
1   {"\\x00e14a408baf7f453312eec68e9b7d728ec5337fb...   
27  {"\\x01390fd803c110ac71730ece1decfc34eb1d0088e...   
28  {"\\x0099cd8bde557814842a3121e8ddfd433a539b8c9...   
29  {"\\x0099cd8bde557814842a3121e8ddfd433a539b8c9...   

                                                 data            event_name  \
0   {"\\x08d27bea7c176d9903","\\x00","\\x9073251f0...                  Sync   
1   {"\\x03b253b20be774a452","\\x00","\\x38d5cc00a...                  Sync   
27  {"\\x00","\\x8718bf271493c557974f8aab1179f431a...  OwnershipTransferred   
28                                {"\\x03e8","\\x00"}              Transfer   
29                          {"\\x0beaeb60e8","\\x00"}              Transfer   

                                         decoded_data   timestamp  
0   {"reserve_0": 162740926578466593027, "reserve_...  1709771770  
1   {"reserve_0": 68190042147144377426, "reserve_1...  1711609199  
27  {"new_owner": "0x008718bf271493c557974f8aab117...  1705929814  
28  {"to": "0x000000000000000000000000000000000000...  1705932348  
29  {"to": "0x06c364fa52256aa61cfa0c8a38e34f24cd87...  1705932348

In [113]:
swaps = nostra_df[swap_mask]

In [123]:
json.loads(swaps['decoded_data'][401])['sender']

'0x06720b763aac6608ceba3f9069bebb0f990cd96b26071b3fa2a2109940f90db2'

In [120]:
swaps['decoded_data'][184]

'{"to": "0x07914e79623255d42664d24a501a66a7479e3b1079103d0d647a01b84fc5f942", "sender": "0x06720b763aac6608ceba3f9069bebb0f990cd96b26071b3fa2a2109940f90db2", "amount_0_in": 0, "amount_1_in": 114153752, "amount_0_out": 50330896770033963, "amount_1_out": 0}'

In [124]:

def get_amount(decoded_data):
    data = json.loads(decoded_data)
    # eth = data['amount_0_in'] if data['amount_0_in'] > 0 else data['amount_0_out']
    usdc = (data['amount_1_in'] / 10**6) if data['amount_1_in'] > 0 else (data['amount_1_out'] / 10**6)
    return usdc

swaps['usdc_volume'] = swaps['decoded_data'].apply(get_amount)

/var/folders/zp/9kkn3ltx55q4wz7hp7q19ggm0000gn/T/ipykernel_5689/4227175175.py:7: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  swaps['usdc_volume'] = swaps['decoded_data'].apply(get_amount)


In [125]:
swaps.head()

block_number  transaction_index  event_index  \
184        522020                 48            9   
186        522020                 48           18   
188        522020                 48           36   
190        522020                 48           27   
401        522057                  0           38   

                                            class_hash  \
184  0652ad70e5978e84fb886ebe5a0a85f2352281b67488b4...   
186  0652ad70e5978e84fb886ebe5a0a85f2352281b67488b4...   
188  0652ad70e5978e84fb886ebe5a0a85f2352281b67488b4...   
190  0652ad70e5978e84fb886ebe5a0a85f2352281b67488b4...   
401  0652ad70e5978e84fb886ebe5a0a85f2352281b67488b4...   

                                      contract_address  \
184  05ef8800d242c5d5e218605d6a10e81449529d4144185f...   
186  05ef8800d242c5d5e218605d6a10e81449529d4144185f...   
188  05ef8800d242c5d5e218605d6a10e81449529d4144185f...   
190  05ef8800d242c5d5e218605d6a10e81449529d4144185f...   
401  05ef8800d242c5d5e218605d6a10e81449529d4144185f...   

                                                  keys  \
184  {"\\x00e316f0d9d2a3affa97de1d99bb2aac0538e2666...   
186  {"\\x00e316f0d9d2a3affa97de1d99bb2aac0538e2666...   
188  {"\\x00e316f0d9d2a3affa97de1d99bb2aac0538e2666...   
190  {"\\x00e316f0d9d2a3affa97de1d99bb2aac0538e2666...   
401  {"\\x00e316f0d9d2a3affa97de1d99bb2aac0538e2666...   

                                                  data event_name  \
184  {"\\x06720b763aac6608ceba3f9069bebb0f990cd96b2...       Swap   
186  {"\\x06720b763aac6608ceba3f9069bebb0f990cd96b2...       Swap   
188  {"\\x06720b763aac6608ceba3f9069bebb0f990cd96b2...       Swap   
190  {"\\x06720b763aac6608ceba3f9069bebb0f990cd96b2...       Swap   
401  {"\\x06720b763aac6608ceba3f9069bebb0f990cd96b2...       Swap   

                                          decoded_data   timestamp  \
184  {"to": "0x07914e79623255d42664d24a501a66a7479e...  1706414784   
186  {"to": "0x07914e79623255d42664d24a501a66a7479e...  1706414784   
188  {"to": "0x07914e79623255d42664d24a501a66a7479e...  1706414784   
190  {"to": "0x07914e79623255d42664d24a501a66a7479e...  1706414784   
401  {"to": "0x07914e79623255d42664d24a501a66a7479e...  1706418519   

     usdc_volume  
184   114.153752  
186   114.908772  
188   115.755224  
190   115.443982  
401   116.745859

In [126]:
swaps.usdc_volume.describe()

count    47453.000000
mean       118.523377
std        387.537201
min          0.000021
25%         11.926803
50%         39.230644
75%        105.241746
max      43459.190827
Name: usdc_volume, dtype: float64

In [132]:
min_swap_data = swaps[swaps.usdc_volume == swaps.usdc_volume.min()].decoded_data
min_swap_data

232998    {"to": "0x04270219d365d6b017231b52e92b3fb5d7c8...
Name: decoded_data, dtype: object

In [136]:
json.loads(min_swap_data.iloc[0])['amount_0_out'] / 10 ** 18

6.615048176e-09

In [145]:
swaps_per_block = swaps.groupby('block_number').agg({'usdc_volume': 'sum', 'decoded_data': 'count', 'timestamp': 'max'}).reset_index()

In [146]:
swaps_per_block.head()

block_number  usdc_volume  decoded_data   timestamp
0        516225     9.000000             1  1706018147
1        516236    18.000000             1  1706018621
2        520410   354.051797             3  1706303613
3        520411   230.654820             2  1706303708
4        520431   229.092141             2  1706305195

In [147]:
swaps_per_block.rename(columns={'decoded_data': 'swap_count'}, inplace=True)

In [149]:
swaps_per_block['datetime'] = pd.to_datetime(swaps_per_block['timestamp'], unit='s')

In [150]:
swaps_per_block.to_csv('swaps_per_block.csv', index=False)